In [2]:
import io
import progressbar
import os
import struct

In [3]:
class Constants:
    def __init__(self, max_bits = 18, ceil = 7):
        self.max_bits = max_bits
        self.ceil = ceil

In [44]:
class LZW:
    def __init__(self, max_bits = 18, ceil = 7):
        self.constants = Constants(max_bits, ceil)
        self.letters_counts={}
        self.file_str = ''
        self.file_path = ''
        self.codes = {}
        self.out_codes = {}
        self.output = ''
        self.decoded = ''
        self.max_length = 2**self.constants.max_bits
        self.main_length = 0
        self.ceil = self.constants.ceil
        self.main_codes = {}
        self.main_out_codes = {}
    
    
    def readFile(self, file_path):
        self.file_path = file_path
        self.file_str = io.open(file_path, mode="r", encoding="utf-8").read()
        self.file_str = self.file_str.replace('\n','\r\n')
        let_count = 1
        for let in self.file_str:
            if self.letters_counts.has_key(let):
                self.letters_counts[let] = self.letters_counts[let] + 1
            else:
                self.letters_counts[let] = 1
                self.codes[let] = len(self.codes)
        self.out_codes = {v: k for k, v in self.codes.iteritems()}
        self.main_codes = self.codes.copy()
        self.main_out_codes = self.out_codes.copy()
        self.main_length = len(self.codes)
                
            
    def encode(self):
        s = self.file_str[0]
        i = 1
        with progressbar.ProgressBar(max_value=len(self.file_str)) as bar:
            while i<len(self.file_str):
                c = self.file_str[i]
                if self.codes.get(s+c, None) != None:
                    s = s+c
                else:
                    bits = bin(self.codes[s])[2:]
                    self.output += bits.zfill(self.ceil)
                    self.codes[s+c] = len(self.codes)
                    s = c
                    
                if len(self.codes) >= 2**self.ceil:
                    self.ceil += 1

                #if len(self.codes) >= self.max_length:
                 #   self.codes = self.main_codes.copy()
                  #  self.ceil = 7

                i += 1
                bar.update(i)
        bits = bin(self.codes[s])[2:]
        self.output += bits.zfill(self.ceil)
        
        
    def decode(self):
        self.ceil = 7
        s = None
        i = 0
        with progressbar.ProgressBar(max_value=len(self.output)) as bar:
            while i< len(self.output):
                k = int(self.output[i: i+self.ceil], 2)
                try:
                    entry = self.out_codes[k]
                except KeyError:
                    entry = s + s[0]

                self.decoded += entry

                if s != None:
                    self.out_codes[len(self.out_codes)] = s+entry[0]
                    
                if len(self.out_codes) >= 2**self.ceil:
                    self.ceil += 1

                #if len(self.out_codes) >= self.max_length:
                 #   self.out_codes = self.main_out_codes.copy()
                  #  self.ceil = 7

                s = entry
                i += self.ceil
                bar.update(i)
                
    def printEncodedFile(self, name = 'encoded_file.bin'):
        newFile = open(name, "wb")
        newFile.write(struct.pack('{}H'.format(len(self.output)), *self.output))
        newFile.close()
        
    def printTryFile(self):
        str_to_print = ''
        i = 0
        while i < len(self.output):
            str_to_print += unichr(int(self.output[i: i+8], 2))
            i += 8
        file_to_print = io.open('omar.txt', mode="w", encoding="utf-8")
        file_to_print.write(str_to_print)
        file_to_print.close()
        print 'Done!'
            
            
    def calculateCompressionRatio(self):
        return float(os.path.getsize(self.file_path))/(len(self.output) / 8.0)

In [45]:
model = LZW()
model.readFile('DataSet/DataSet_6.tsv')
print model.file_str
#print sys.getsizeof(encoder.file_str)
#os.path.getsize(encoder.file_path)

 تسونامي من المشاعر أو قل طاقة الألم و الهم و اتفتحت في وجهك أشعر بأنها أقرب إلى قصيدة سوداء رائعة منها إلى رواية في غرناطة تجعلك رضوى تسير في الشوارع بحق و تشم رائحة الطعام ينضج .تشعرك بالألم أيضا لكن الطنطورية شئ آخر. تشعرك و كأن لم تشعر بالألم من قبل في كثير من المراحل الزمنية داخل الرواية كنت أتهيب مجرد فكرة فتح الكتاب.كنت أشعر بالهم بمجرد أن ألمس الغلاف.التشرد و مواجهة الإقتلاع من الجزور ليس الشئ الوحيد الذي تواجهه إن كنت فلسطينيا من عرب الثمانية و الأربعين المهجرين .فقد كتب عليك الشقاء.ما أن يستقيم لك الحال نوعا ما في بلد كلبنان مثلا حتى تدخل في متاهة أخرى مرسومة باللون الأحمر .حرب أهلية و اجتياح صهيوني ناهيك عن التناحر بين الفصائل الفلسطينية ذاتها . يهاجر أبناءك كل لسبب و كل في وجهة أيضا .تذهب من أجل هذا هنا و تذهب من جل ذاك هناك و لا يطيب لك مقام هل سبب الشعور بالألم المبالغ فيه أن المكتوب ليس من مجريات الماضي البعيد إنما أحداث رأيت تبعاتها و عاصرها أبيك و جدك من ثم تشعر بالعار؟ صدقا لا أعرف على مدار فصول الرواية كما الحال في غرناطة تشعر بروعة الكاتبة خاصة في إيرادها تعبيرات تح

In [46]:
model.encode()

100% (998133 of 998133) |################| Elapsed Time: 0:00:33 Time:  0:00:33


In [47]:
print model.calculateCompressionRatio()

3.95874403576


In [8]:
model.decode()

100% (3613829 of 3613829) |##############| Elapsed Time: 0:00:43 Time:  0:00:43


In [9]:
print model.decoded

 تسونامي من المشاعر أو قل طسقة الألم و الهم و اتفتحت في وجهك أشعر بأنها أقرب إلى قصيدة سوداء رائعة منها إلى رواية في غرناطة تجعلك رضوى تسير في الشوارع بحق و تشم رائحة الطعام ينضج .تشعرك بالألم أيضا لكن الطسطورية شئ آخر. تشعرك و كأن لم تشعر بالألم من قبل في كثير من المراحل الزمنية داخل الرواية كنت أتهيب مجرد فكرة فتح الكتاب.كنت أشعر بالهم بمجرد أن ألمس الغلاف.التشرد و مواجهة الإقتلاع من الجزور ليس الشئ الوحيد الذي تواجهه إن كنت فلسطينيا من عرب الثمانية و الأربعين المهجرين .فقد كتب عليك الشقاء.ما أن يستقيم لك الحال نوعا ما في بلد كلبنان مثلا حتى تدخل في متاهة أخرى مرسومة باللون الأحمر .حرب أهلية و اجتياح صهيوني ناهيك عن التناحر بين الفصائجهفلسطينية ذاتها . يهاجر أبناءك كل لسبب و كل في وجهة أيضا .تذهب من أجل هذا هنا و تذهب من جل ذاك هناك و لا يطيب لك مقام هل سبب الشعور بالألم المبالغ فيه أن المكتوب ليس من مجريات الماضي البعيد إنما أحداث رأيت تبعاتها و عاصرها أبيك و جدك من ثم تشعر بالعار؟ صدقا لا أعرف على مدار فصول الرواية كما الحال في غرناطة تشعر بروعة الكاتبة خاصة في إيرادها تعبيرات تحتا

In [48]:
model.printTryFile()

Done!


In [49]:
model2 = LZW(ceil = 8)
model2.readFile('omar.txt')
print model2.file_str

 0C   ¢	
(XÀ
 p(h{@cÓ4; `£ÀK° ¨` +ÀhX¨ °@»ØÀ8Ì8È(Ð X(ØTu
=M (<  à[HtPDÈXèS0;¾MøXTèl`L]¨ØpSP 8 è ÷´È«,X`8ík8°@ Ø > ©°ZdôOÏ#»Õ7Â§ÖPBÔ6¿KPôâ"7A"	@ ¿  ` S`°ÊL(a$a@*M¡ÉÔJ,+<
ïp8CÇLô_¥ÜÀ°4ZmÆÎ!1
(«µàçIZ 60ANo¥¤Á  s°¢Ç
"PS±Osà6FS3 é¸5dÈU` 4f ÂG é6¨qÝ *i75 E¤$Íj8A*À³8`ÀUàR À&ÄÉ Øi¦AR@	§ÄÌB!²^°¬;$A`*pQ!9B	dLë

È<J¬Áõ! ª ú@À  4ðüB D`LÅ * @;S6`3PE¼  
dÚàìÊ09&8Ê0®IÚÎ@ìÈ
*Ë§à°Õ»ÅBZ$.@åØôt Yv­)	$Ê6Ç¡¤â0ta#Úµ¨ð; ê&¨0¥éAXâÚÃ!Ò.
,
A 
C`,j  Év Sk3 (ï/äéwJ&ÄÐÃÀ#`j:<Dùv­-9¢æF
|v
¥­$¸J`r  0 ¤6S°42`~ÕÕ¦y~X£z¾¼k@ú_ý«FxÛt]H-\u Èú`s
÷d¶cH À8jM!ï¸+5¹#¹J·Uh¸ìLý$)8`6 kÁ·=Òa@LÁyFç¤jo Ë;`¨A C +)·ÄÙ³aÁ	Ewà=blú2­%Tjh8?nÞÞp3ù GäèGëÀ]äcR^ eqHÓç%Huh&
LÊHhcª..TÄ&àâ8\	LlÈP9@@ñBÊö

In [50]:
model2.encode()

100% (456263 of 456263) |################| Elapsed Time: 0:00:57 Time:  0:00:57


In [51]:
model2.calculateCompressionRatio()

1.2123812664801679

In [53]:
model.calculateCompressionRatio()*model2.calculateCompressionRatio()/8


0.5999383884679164

In [107]:
print len(model.output)/8.0

353329.875


In [108]:
print len(model2.output)/8.0

377800.0
